# League of Legends Predictor

**Name(s)**: Jawad Najar and Ali Boussi

**Website Link**: (your website link)

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px

pd.options.plotting.backend = 'plotly'
pd.set_option('display.max_columns', None)

## Step 1: Introduction

###

In [2]:
raw_data = pd.read_csv('data.csv')
raw_data.head()

/var/folders/_h/74y4pfyn6j36pp57yqqzprl80000gn/T/ipykernel_13774/3741442452.py:1: DtypeWarning: Columns (2) have mixed types. Specify dtype option on import or set low_memory=False.
  raw_data = pd.read_csv('data.csv')


gameid datacompleteness  url league  year   split  playoffs  \
0  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   
1  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   
2  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   
3  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   
4  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   

                  date  game  patch  participantid  side position playername  \
0  2022-01-10 07:44:08     1  12.01              1  Blue      top     Soboro   
1  2022-01-10 07:44:08     1  12.01              2  Blue      jng     Raptor   
2  2022-01-10 07:44:08     1  12.01              3  Blue      mid     Feisty   
3  2022-01-10 07:44:08     1  12.01              4  Blue      bot      Gamin   
4  2022-01-10 07:44:08     1  12.01              5  Blue      sup      Loopy   

                                    playerid           teamname  \
0  oe:player:38e0af7278d6769d0c81d7c4b47ac1e  BRION Challengers   
1  oe:player:637ed20b1e41be1c51bd1a4cb211357  BRION Challengers   
2  oe:player:d1ae0e2f9f3ac1e0e0cdcb86504ca77  BRION Challengers   
3  oe:player:998b3e49b01ecc41eacc392477a98cf  BRION Challengers   
4  oe:player:e9741b3a238723ea6380ef2113fae63  BRION Challengers   

                                    teamid  champion   ban1     ban2    ban3  \
0  oe:team:733ebb9dbf22a401c0127a0c80193ca  Renekton  Karma  Caitlyn  Syndra   
1  oe:team:733ebb9dbf22a401c0127a0c80193ca  Xin Zhao  Karma  Caitlyn  Syndra   
2  oe:team:733ebb9dbf22a401c0127a0c80193ca   LeBlanc  Karma  Caitlyn  Syndra   
3  oe:team:733ebb9dbf22a401c0127a0c80193ca    Samira  Karma  Caitlyn  Syndra   
4  oe:team:733ebb9dbf22a401c0127a0c80193ca     Leona  Karma  Caitlyn  Syndra   

     ban4  ban5 pick1 pick2 pick3 pick4 pick5  gamelength  result  kills  \
0  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      2   
1  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      2   
2  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      2   
3  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      2   
4  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      1   

   deaths  assists  teamkills  teamdeaths  doublekills  triplekills  \
0       3        2          9          19          0.0          0.0   
1       5        6          9          19          0.0          0.0   
2       2        3          9          19          0.0          0.0   
3       4        2          9          19          0.0          0.0   
4       5        6          9          19          0.0          0.0   

   quadrakills  pentakills  firstblood  firstbloodkill  firstbloodassist  \
0          0.0         0.0         0.0             0.0               0.0   
1          0.0         0.0         1.0             0.0               1.0   
2          0.0         0.0         0.0             0.0               0.0   
3          0.0         0.0         1.0             0.0               1.0   
4          0.0         0.0         1.0             1.0               0.0   

   firstbloodvictim  team kpm    ckpm  firstdragon  dragons  opp_dragons  \
0               0.0    0.3152  0.9807          NaN      NaN          NaN   
1               0.0    0.3152  0.9807          NaN      NaN          NaN   
2               0.0    0.3152  0.9807          NaN      NaN          NaN   
3               0.0    0.3152  0.9807          NaN      NaN          NaN   
4               0.0    0.3152  0.9807          NaN      NaN          NaN   

   elementaldrakes  opp_elementaldrakes  infernals  mountains  clouds  oceans  \
0              NaN                  NaN        NaN        NaN     NaN     NaN   
1              NaN                  NaN        NaN        NaN     NaN     NaN   
2              NaN                  NaN        NaN        NaN     NaN     NaN   
3              NaN                  NaN     

In [3]:
raw_data.shape

(150588, 161)

In [4]:
raw_data['gameid'].nunique()

12549

<p>How does the way a team plays affect how long a game lasts?</p>


## Step 2: Data Cleaning and Exploratory Data Analysis

#### Data Cleaning

In [5]:
df = raw_data.copy()

# filter for complete data
df = df[df['datacompleteness'] == 'complete']

# drop unnecessary columns (metadata)
meta_columns = ['participantid', 'playerid', 'teamid', 
                'datacompleteness', 'url', 'date',
                'teamname', 'playername']
df = df.drop(columns=meta_columns)

# seperate team and player stats
team_df = df[df['position'] == 'team']
player_df = df[df['position'] != 'team']

# Dropping all columnsn that are all NaN (it is a team/player stat, respectively)
player_df = player_df.dropna(axis=1, how='all')
team_df = team_df.dropna(axis=1, how='all')

team_df['game_length_min'] = team_df['gamelength'] / 60
player_df['game_length_min'] = player_df['gamelength'] / 60

# Team Adv columns 
team_df['tower_advantage'] = team_df['towers'] - team_df['opp_towers']
team_df['inhibitor_advantage'] = team_df['inhibitors'] - team_df['opp_inhibitors']

In [6]:
fig = px.histogram(
    team_df,
    x='game_length_min',
    nbins=15,  
    title='Distribution of Game Lengths (minutes)'
)

fig.update_layout(
    bargap=0.1, 
    template='plotly_white',  
    xaxis_title='Game Length (minutes)',
    yaxis_title='Number of Games',
    font=dict(size=14)
)

fig.show()

In [7]:
fig.write_image("assets/univariate.png", format="png", scale=2)

In [8]:
# Deciding against imputation here, as NaN values represent that a game has ended prior to that time
# and we want to keep that information
gold_diff_columns = ['golddiffat10', 'golddiffat15', 'golddiffat20']
xp_diff_columns = ['xpdiffat10', 'xpdiffat15', 'xpdiffat20']

# Creating 3 features that we will plot against one another in the future
player_df['avg_xpdiff'] = player_df[xp_diff_columns].mean(axis=1, skipna=True)
player_df['avg_golddiff'] = player_df[gold_diff_columns].mean(axis=1, skipna=True)

In [9]:
fig = px.histogram(
    team_df,
    x='tower_advantage',
    nbins=15,  
    title='Distribution of Tower Advantage',
    labels={'tower_advantage': 'Tower Advantage (Team - Opponent)'},
    color_discrete_sequence=['indianred'] 
)

fig.update_layout(
    bargap=0.1, 
    template='plotly_white',  
    xaxis_title='Tower Advantage',
    yaxis_title='Number of Games',
    font=dict(size=14)
)

fig.show()

In [10]:
fig = px.histogram(
    team_df,
    x='inhibitor_advantage',
    nbins=15, 
    title='Distribution of Inhibitor Advantage',
    labels={'inhibitor_advantage': 'Inhibitor Advantage (Team - Opponent)'},
    color_discrete_sequence=['skyblue'] 
)

fig.update_layout(
    bargap=0.1, 
    template='plotly_white', 
    xaxis_title='Inhibitor Advantage',
    yaxis_title='Number of Games',
    font=dict(size=14)
)

fig.show()

In [11]:
# Here, we will sample 10% of the games
wins = player_df[player_df['result'] == 1]
all_games = wins['gameid'].drop_duplicates()
sampled_games = all_games.sample(frac=0.1, random_state=98)
sampled_df = wins[wins['gameid'].isin(sampled_games)]

In [12]:
fig = px.scatter(
    sampled_df,
    x='game_length_min',
    y='avg_xpdiff',
    color='position',
    title='Game Length (minutes) vs Average XP Difference by position (Winning Games)',
    labels={'avg_xpdiff': 'Average XP Difference', 'game_length_min': 'Game Length (minutes)'},
    template='plotly_white',
    hover_data=['position']
)

fig.update_layout(
    xaxis_title='Game Length (minutes)',
    yaxis_title='Average XP Difference',
    font=dict(size=14)
)

fig.show()

In [13]:
fig = px.scatter(
    sampled_df,
    x='game_length_min',
    y='avg_golddiff',
    color='position',
    title='Game Length (minutes) vs Average Gold Difference by position (Winning Games)',
    labels={'game_length_min': 'Game Length (minutes)', 'avg_golddiff': 'Average Gold Difference'},
    template='plotly_white',
    hover_data=['position']
)

fig.update_layout(
    xaxis_title='Game Length (minutes)',
    yaxis_title='Average Gold Difference',
    font=dict(size=14)
)

fig.show()

In [14]:
sampled_games = team_df.sample(frac=0.1, random_state=98)
fig = px.scatter(
    sampled_games,
    x='totalgold',
    y='game_length_min',
    title='Total Gold vs Game Length (minutes)',
    labels={'totalgold': 'Total Gold', 'game_length_min': 'Game Length (minutes)'},
    template='plotly_white',
    hover_data=['position']
)

fig.update_layout(
    xaxis_title='Total Gold',
    yaxis_title='Game Length (minutes)',
    font=dict(size=14)
)

In [15]:
fig.write_image("assets/bivariate.png", format="png", scale=2)

In [ ]:
# Creating a pivot table for game length (in minutes) by champion and position
pd.pivot_table(
    player_df,
    index='champion',
    columns='position',
    values='game_length_min',
).sort_values(by='champion', ascending=True)

position        bot        jng        mid        sup        top
champion                                                       
Aatrox    25.016667        NaN  30.304167        NaN  31.183804
Ahri      26.733333  23.950000  31.990258        NaN  28.105556
Akali     26.166667        NaN  31.265598        NaN  32.897105
Akshan          NaN        NaN  31.043122        NaN  32.017708
Alistar         NaN        NaN        NaN  31.779657        NaN
...             ...        ...        ...        ...        ...
Zeri      32.034734  34.158333  31.758120        NaN  32.107500
Ziggs     31.275634        NaN  31.318478  32.666667  31.750000
Zilean    28.516667        NaN  30.944133  32.271940  31.410784
Zoe             NaN        NaN  32.022768  33.700000        NaN
Zyra            NaN        NaN        NaN  32.644792        NaN

[162 rows x 5 columns]

## Step 3: Framing a Prediction Problem

<p> Can we accurately predict the length of a League of Legends game using postgame data? </p>

## Step 4: Baseline Model

In [17]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from sklearn.ensemble import RandomForestRegressor

In [18]:
features = [
    'totalgold',
    'earnedgold',
    'minionkills',
    'team kpm',
    'ckpm',
    'cspm',
    'deaths',
    'earned gpm',
    'visionscore',
    'monsterkills',
    'damagetochampions',
    'teamkills',
    'vspm',
    'wardsplaced',
    'dpm',
    'goldspent',
    'wpm'
]
X = team_df[features]
y = team_df['gamelength']

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, stratify=y, random_state=42
)

In [19]:
len(features)

17

In [20]:
rf = RandomForestRegressor(random_state=42)
rf.fit(X_train, y_train)

RandomForestRegressor(random_state=42)

In [21]:
y_pred = rf.predict(X_test)
print("MSE:", mean_squared_error(y_test, y_pred))

MSE: 295.9725804832277


## Step 5: Final Model

In [22]:
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler, QuantileTransformer, FunctionTransformer
from sklearn.linear_model import Lasso
from sklearn.compose import make_column_transformer

In [23]:
for feature in features:
    fig = px.histogram(
        team_df, 
        x=feature, 
        nbins=30, 
        title=f'Distribution of {feature}', 
        labels={feature: feature.capitalize()},
        template='plotly_white'
    )
    fig.update_layout(
        xaxis_title=feature.capitalize(),
        yaxis_title='Frequency',
        font=dict(size=14)
    )
    fig.show()

In [24]:
non_normal_features = [
    "team kpm",         # Right-skewed
    "ckpm",             # Right-skewed
    "deaths",           # Left-skewed
    "earned gpm",       # Bimodal
    "damagetochampions",# Right-skewed
    "teamkills"         # Left-skewed
]

col_trans = make_column_transformer(
    (QuantileTransformer(output_distribution='normal'), non_normal_features),
    remainder='passthrough'
)

svr_pipeline = make_pipeline(
    col_trans,
    StandardScaler(),
    Lasso(alpha=0.1, random_state=42),
)

In [25]:
# Hyperparameter tuning
param_grid = {
    "lasso__alpha":      np.logspace(-3, 1, 20),
    "lasso__selection":  ["cyclic", "random"],
    "lasso__fit_intercept": [True, False],
    "lasso__max_iter":   [10_000, 100_000],
    "lasso__tol":        [1e-4, 1e-5],
    "lasso__positive":   [False, True],
}

grid = GridSearchCV(svr_pipeline, param_grid, cv=5, scoring='neg_mean_squared_error', n_jobs=-1)
grid.fit(X_train, y_train)
print("Best alpha:", grid.best_params_)

/Users/boussi/miniforge3/envs/pds/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:697: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.961e+09, tolerance: 5.121e+06
  model = cd_fast.enet_coordinate_descent(
/Users/boussi/miniforge3/envs/pds/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:697: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 7.319e+09, tolerance: 5.118e+06
  model = cd_fast.enet_coordinate_descent(
/Users/boussi/miniforge3/envs/pds/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:697: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider

Best alpha: {'lasso__alpha': 0.0026366508987303583, 'lasso__fit_intercept': True, 'lasso__max_iter': 10000, 'lasso__positive': False, 'lasso__selection': 'cyclic', 'lasso__tol': 1e-05}


In [26]:
# Finding the most influential features
best_pipeline = grid.best_estimator_
coefficients = best_pipeline.named_steps['lasso'].coef_
intercept = best_pipeline.named_steps['lasso'].intercept_
feature_names = X_train.columns

coef_df = pd.DataFrame({
    'feature': feature_names,
    'coefficient': coefficients
}).sort_values(by='coefficient', key=abs, ascending=False)

print(coef_df)

              feature  coefficient
6              deaths  1119.447250
7          earned gpm  -842.972484
8         visionscore     1.466999
9        monsterkills    -0.876953
4                ckpm     0.445371
11          teamkills     0.440286
10  damagetochampions     0.425830
15          goldspent     0.319393
14                dpm    -0.301168
12               vspm    -0.240363
1          earnedgold    -0.235542
13        wardsplaced     0.224892
2         minionkills     0.142239
16                wpm    -0.126032
5                cspm     0.110888
3            team kpm    -0.067286
0           totalgold    -0.017551


In [28]:
y_pred = grid.predict(X_test)
print("MSE:", mean_squared_error(y_test, y_pred))

MSE: 0.05571888257792908
